In [1]:
import geopandas
import altair

altair.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

In [2]:
socal_roads = geopandas.read_file(
    "/home/ian/Downloads/socal-latest-free.shp.zip",
    bbox=(-118.3, 34.12, -118.28, 33.77),
    layer="gis_osm_roads_free_1",
)

In [3]:
vermont = socal_roads[
    socal_roads.name.str.lower().str.contains("vermont avenue") &
    socal_roads.name.notna()
]

In [4]:
FEET_PER_MILE = 5280.
SOCAL_FEET = 2229 # California state plane coordinate system in feet
WGS84 = 4326 # WGS84 coordinate system (lat/lon)

In [5]:
vermont_feet = vermont.to_crs(epsg=SOCAL_FEET).unary_union.buffer(200)

In [6]:
blocks = geopandas.read_file("zip:///home/ian/Downloads/Census_Blocks_2010-shp.zip")

In [7]:
blocks_near_vermont = (
    blocks
    [blocks.intersects(vermont_feet.buffer(FEET_PER_MILE))]
    .assign(**{
        "Population density (pop/sqmi)": lambda x: x.POP_2010/(x.area/FEET_PER_MILE/FEET_PER_MILE),
        "distance": lambda x: x.distance(vermont_feet)
    })
    .to_crs(epsg=WGS84)
    .filter(
        ["POP_2010", "Population density (pop/sqmi)", "distance", "COMM", "geometry"]
    ).rename(columns={"POP_2010": "Population","COMM": "Community"})
)

In [8]:
slider = altair.binding_range(min=0, max=FEET_PER_MILE, step=250, name='Distance from Vermont Avenue (ft):')
selector = altair.selection_single(
    name="cutoff",
    bind=slider,
    init={'cutoff': 1000}
)

In [9]:
vermont_chart = altair.Chart(vermont.unary_union).mark_geoshape(
    stroke="maroon",
    strokeWidth=3,
    fillOpacity=0,
)

In [23]:
text_chart = altair.Chart(blocks_near_vermont).mark_text(fontSize=16).transform_filter(
    altair.datum.distance <= selector.cutoff
).transform_aggregate(
    total="sum(Population)"
).transform_calculate(
    label="'Total population within ' + format(cutoff.cutoff, ',') + ' feet: ' + format(datum.total, ',')"
).encode(
    x=altair.value(5),
    y=altair.value(5),
    text="label:N",
)

In [24]:
block_chart = altair.Chart(blocks_near_vermont).mark_geoshape().encode(
    color=altair.condition(
        altair.datum.distance <= selector.cutoff,
        altair.Color("Population density (pop/sqmi):Q", scale=altair.Scale(domain=[0,100_000])),
        altair.ColorValue('lightgray'),
    ),
    tooltip=[
        "Community",
        altair.Tooltip("Population", format=","),
        altair.Tooltip("Population density (pop/sqmi)", format=",.0f"),
    ],
)


altair.layer(
    block_chart,
    vermont_chart,
    text_chart
).add_selection(
    selector
).configure_view(
    stroke=None
).project(
    type="mercator",
    center=[-118, 34],
    rotate=[0.,-72]
).properties(
    width=1000,
    height=200,
)

alt.LayerChart(...)